# Shortterm Load Prediction using Transfer Learning

In [1]:
# Import python libraries
#
import pandas as pd
import numpy as np
import importlib
from tqdm import tqdm
import pickle
import holidays
import pytz

# Imports own modules.
# All imports are done relative to the root of the project.
# Therefore please add the project root to your environment variables.
#
import forecasting.Model as model
import data.weather_data as weather_data
import data.demandprofiles_readout as demandprofiles
import data.standardprofiles_readout as standardprofiles
import forecasting.LstmAdapter as LstmAdapter
import forecasting.visualization as visualization


2024-04-29 14:43:45.804264: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-29 14:43:45.895707: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-29 14:43:45.897310: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-04-29 14:43:47.016922: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [2]:
importlib.reload(weather_data)
importlib.reload(demandprofiles)
importlib.reload(standardprofiles)
importlib.reload(LstmAdapter)

# Readout the preprocessed power profiles
#
household_loads_train = pd.read_pickle('../data/preprocessed/loadprofiles_1h_train.pkl')
household_loads_test = pd.read_pickle('../data/preprocessed/loadprofiles_1h_test.pkl')
household_loads_train['Aggregated_Power'] = household_loads_train.sum(axis=1)
powerProfile = -1.0 * household_loads_train['Aggregated_Power']

# Readout the weather data
#
startDate = powerProfile.index[0].to_pydatetime().replace(tzinfo=None)
endDate = powerProfile.index[-1].to_pydatetime().replace(tzinfo=None)
weather_measurements = weather_data.WeatherMeasurements()
weatherData = weather_measurements.get_data(
            startDate = startDate, 
            endDate = endDate,
            lat = 51.4817,      # Location:
            lon = 7.2165,       # Bochum Germany,
            alt = 102,          # Meteostat weatherstation   
            sample_periode = 'hourly', 
            tz = 'Europe/Vienna',
            )
selected_columns = ['temp', 'prcp', 'wspd', 'tsun']     # select weather data
weatherData = weatherData.loc[:, selected_columns]

# Load the public holiday calendar
public_holidays_dict = holidays.CountryHoliday('DE', years=range(2013, 2014))
public_holidays_timestamps = [pd.Timestamp(date, tzinfo=pytz.timezone('Europe/Vienna')) for date in public_holidays_dict.keys()]

# Bring the aggregated characteristic power profiles to the format needed by the model
#
lstmAdapter = LstmAdapter.LstmAdapter(public_holidays_timestamps, train_size = 263, dev_size = 0, 
                                            add_tda_features=False, addLaggedPower=True, 
                                            shuffle_data=False, seed=0)
X_model, Y_model = lstmAdapter.transformData(powerProfile, weatherData)

# Readout the standard power profiles (for pretraining)
# and bring it to the format needed by the model
#
demandProfiles_Readout = standardprofiles.StandardProfiles_Readout()
standardprofiles_scaled = demandProfiles_Readout.get_scaled_standardprofiles(powerProfile)
lstmAdapter_pretrain = LstmAdapter.LstmAdapter(public_holidays_timestamps, train_size = 263, dev_size = 0, 
                                            add_tda_features=False, addLaggedPower=True, 
                                            shuffle_data=False, seed=0)
X_model_pretrain, Y_model_pretrain = lstmAdapter_pretrain.transformData(standardprofiles_scaled, None)


In [3]:
importlib.reload(model)
importlib.reload(visualization)

# Pretrain the power profile model
#
pretrain_model = False
if pretrain_model == True:

    optimizer = model.Optimizer(maxEpochs=300, set_learning_rates=[0.015, 0.005, 0.003, 0.002, 0.001, 0.001, 0.001])
    model_pretraining = model.Model(optimizer, reg_strength = 0.00)
    model_pretraining.compile(metrics=[])
    history_pretraining = model_pretraining.model.fit(x=X_model_pretrain['train'], y=Y_model_pretrain['train'], 
                        validation_data=(X_model_pretrain['dev'], Y_model_pretrain['dev']),
                        batch_size=optimizer.miniBatchSize,
                        epochs=optimizer.maxEpochs,
                        shuffle=True, verbose='auto',
                        callbacks=[
                            optimizer.get_lr_callback(), 
                            #optimizer.get_early_stopping_callbacks()
                            ]
                        )
    
    # Store the results
    #
    model_pretraining.save_weights('lstm_pretrain_weights.h5')
    with open('lstm_pretrain_results.pkl', 'wb') as file:
        pickle.dump((history_pretraining, model_pretraining.model), file)

    # Evaluate the pretrained model
    #
    # plotlyApp = visualization.PlotlyApp(X_model_pretrain, Y_model_pretrain, model_pretraining, lstmAdapter_pretrain)
    # plotlyApp.run(myport=8055)
    

Epoch 1/300


2024-04-09 07:42:50.837070: E tensorflow/compiler/xla/stream_executor/cuda/cuda_driver.cc:268] failed call to cuInit: CUDA_ERROR_NO_DEVICE: no CUDA-capable device is detected


9/9 [==============================] - 8s 71ms/step - loss: 1.8507 - lr: 0.0150
Epoch 2/300
9/9 [==============================] - 1s 67ms/step - loss: 0.3238 - lr: 0.0150
Epoch 3/300
9/9 [==============================] - 1s 69ms/step - loss: 0.1868 - lr: 0.0150
Epoch 4/300
9/9 [==============================] - 1s 72ms/step - loss: 0.1827 - lr: 0.0150
Epoch 5/300
9/9 [==============================] - 1s 69ms/step - loss: 0.1580 - lr: 0.0150
Epoch 6/300
9/9 [==============================] - 1s 67ms/step - loss: 0.0782 - lr: 0.0150
Epoch 7/300
9/9 [==============================] - 1s 66ms/step - loss: 0.0590 - lr: 0.0150
Epoch 8/300
9/9 [==============================] - 1s 70ms/step - loss: 0.0552 - lr: 0.0150
Epoch 9/300
9/9 [==============================] - 1s 68ms/step - loss: 0.0374 - lr: 0.0150
Epoch 10/300
9/9 [==============================] - 1s 67ms/step - loss: 0.0551 - lr: 0.0150
Epoch 11/300
9/9 [==============================] - 1s 68ms/step - loss: 0.0333 - lr: 0.015

In [4]:
# Train with moving horizon
#

# Reload the model module
importlib.reload(model)

# Define the training days. Train not every day-of-year, but
# only the first 14 days and weekly afterwards.
training_days = list(range(1, X_model['all'].shape[0], 7))

def train_on_day(i, use_transfer_learning, X, Y):
    X_past = X['all'][:i, :, :]
    Y_past = Y['all'][:i, :, :]

    optimizer = model.Optimizer(maxEpochs=300, set_learning_rates=[0.015, 0.005, 0.003, 0.002, 0.001, 0.001, 0.001])
    myModel = model.Model(optimizer, reg_strength = 0.00, shape=(X_past.shape[1],X_past.shape[2]))
    myModel.compile(metrics=[])
    if use_transfer_learning == True:
        myModel.load_weights('lstm_pretrain_weights.h5')
    train_history = myModel.model.fit(x=X_past, y=Y_past,
                                    batch_size=X_past.shape[0],
                                    epochs=optimizer.maxEpochs,
                                    shuffle=True,
                                    verbose=0,
                                    callbacks=[
                                        optimizer.get_lr_callback(), 
                                        # optimizer.get_early_stopping_callbacks()
                                        ])

    return myModel, train_history, i

def train_on_day_wrapper(args):
    return train_on_day(*args)

def start_training(use_transfer_learning):
    num_workers = 16
    results = Parallel(n_jobs=num_workers)(
        delayed(train_on_day)(i, use_transfer_learning, X_model, Y_model) for i in training_days
    )

    models_list, train_histories_list, day_indices = zip(*results)
    train_histories = {i: history for i, history in zip(day_indices, train_histories_list)}
    models = {i: model for i, model in zip(day_indices, models_list)}

    return train_histories, models

def evaluate_results(models):
    evaluations = {}
    predictions = {}

    for i in tqdm(range(1, X_model['all'].shape[0]), desc="Evaluation and Prediction Progress"):
        
        # Get the last trained model to a given day
        last_training_day = max(filter(lambda key: key <= i, models.keys()))
        last_available_model = models[last_training_day]

        # Evaluate and predict
        X_future = X_model['all'][i, np.newaxis, :, :]
        Y_future = Y_model['all'][i, np.newaxis, :, :]
        evaluations[i] = last_available_model.model.evaluate(X_future, Y_future, verbose=0)
        predictions[i] = last_available_model.predict(X_future, verbose=0)

    return evaluations, predictions


In [5]:
train_histories, models = start_training(use_transfer_learning=True)

2024-04-09 07:45:57.229372: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-09 07:45:57.250398: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-09 07:45:57.250398: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-09 07:45:57.254094: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-09 07:45:57.265550: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-09 07:45:57.265547: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-09 07:45:57.265550: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-09 07:45:57.265550: I tensorflow/tsl/cud

In [6]:
evaluations, predictions = evaluate_results(models)

Evaluation and Prediction Progress: 100%|██████████| 342/342 [02:48<00:00,  2.03it/s]


In [7]:
train_histories_wo_pretraining, models_wo_pretraining = start_training(use_transfer_learning=False)


2024-04-09 07:52:45.805312: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-09 07:52:45.807236: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-09 07:52:45.835187: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-09 07:52:45.835187: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-09 07:52:45.837629: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-09 07:52:45.862100: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-09 07:52:45.862100: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2024-04-09 07:52:45.862689: I tensorflow/core/pl

In [8]:
evaluations_wo_pretraining, predictions_wo_pretraining = evaluate_results(models_wo_pretraining)


Evaluation and Prediction Progress: 100%|██████████| 342/342 [02:49<00:00,  2.02it/s]


In [9]:
# with open('lstm_results.pkl', 'wb') as file:
#     pickle.dump((predictions, train_histories, evaluations), file)

# with open('lstm_results_wo_pretraining.pkl', 'wb') as file:
#     pickle.dump((predictions_wo_pretraining, train_histories_wo_pretraining, evaluations_wo_pretraining), file)


In [3]:
with open('lstm_results_wo_pretraining.pkl', 'rb') as file:
    (predictions_wo_pretraining, train_histories_wo_pretraining, evaluations_wo_pretraining) = pickle.load(file)

with open('lstm_results.pkl', 'rb') as file:
    (predictions, train_histories, evaluations) = pickle.load(file)

with open('lstm_pretrain_results.pkl', 'rb') as file:
    (history_pretraining, model_pretraining) = pickle.load(file)


2024-04-29 14:44:14.869287: E tensorflow/compiler/xla/stream_executor/cuda/cuda_driver.cc:268] failed call to cuInit: CUDA_ERROR_NO_DEVICE: no CUDA-capable device is detected


In [4]:
# Compare the pretrained and non-pretrained results
#

def get_final_metrics(history):
    return {key: value.history['loss'][-1] for key, value in history.items()}

def get_final_val_metrics(evaluations):
    return evaluations.copy()

def create_trace(x_data, y_data, name):
    return go.Scatter(x=list(x_data.keys()), y=list(y_data.values()), mode='lines', name=name)

def create_layout(title, x_title, y_title):
    return go.Layout(
        title=title,
        xaxis=dict(title=x_title),
        yaxis=dict(title=y_title),
        legend=dict(x=1, y=1, traceorder='normal', orientation='v')  # Adjusted legend position
    )

def create_and_show_figure(traces, layout):
    fig = go.Figure(data=traces, layout=layout)
    fig.show()

# Get final metrics
losses = get_final_metrics(train_histories)
losses_wo_pretraining = get_final_metrics(train_histories_wo_pretraining)
val_losses = get_final_val_metrics(evaluations)
val_losses_wo_pretraining = get_final_val_metrics(evaluations_wo_pretraining)

# Create figures and traces
#
trace_train_loss = create_trace(losses, losses, 'train_loss_with_pretraining')
trace_train_loss_pretraining = create_trace(losses_wo_pretraining, losses_wo_pretraining, 'train_loss_without_pretraining')
trace_val_loss = create_trace(val_losses, val_losses, 'val_loss_with_pretraining')
trace_val_loss_pretraining = create_trace(val_losses_wo_pretraining, val_losses_wo_pretraining, 'val_loss_without_pretraining')
layout_train_loss = create_layout('Training Loss', 'Days', 'MSE')
layout_val_loss = create_layout('Validation Loss', 'Days', 'MSE')
fig_train_loss = go.Figure(data=[trace_train_loss, trace_train_loss_pretraining], layout=layout_train_loss)
fig_val_loss = go.Figure(data=[trace_val_loss, trace_val_loss_pretraining], layout=layout_val_loss)
create_and_show_figure([trace_train_loss, trace_train_loss_pretraining], layout_train_loss)
create_and_show_figure([trace_val_loss, trace_val_loss_pretraining], layout_val_loss)


In [9]:
importlib.reload(visualization)

# Evaluate the finetuned models
#
plotlyApp = visualization.PlotlyApp(X_model, Y_model, None, lstmAdapter, predictions, )#Y_model_pretrain, lstmAdapter_pretrain)
plotlyApp.run(myport=8058)


In [6]:
import plotly.subplots as sp
import plotly.graph_objects as go
import numpy as np

def plot_loss(fig, row_num, histories, first_epoch, last_epoch, skip_first_days):
    for run, history in histories.items():
        if run < skip_first_days:
            print("Day skipped!")
            continue
        loss = np.array(history.history['loss'][first_epoch:last_epoch])
        fig.add_trace(go.Scatter(x=np.arange(len(loss)), y=loss, mode='lines', name=f'Day {run}', showlegend=False), row=row_num, col=1)

first_epoch = 0
last_epoch = -1
first_day = 0

# Create Training
fig = sp.make_subplots(rows=3, cols=1, 
                       subplot_titles=['Training Loss during Pretraining', 
                                       'Training Loss with Transfer Learning',
                                       'Training Loss without Transfer Learning'], 
                        shared_xaxes=True)
# Set the same scale on the y-axis for all subplots
fig.update_yaxes(title_text="Mean Squared Error", row=1, col=1, range=[0, 0.15])     # type='log'
fig.update_yaxes(title_text="Mean Squared Error", row=2, col=1, range=[0, 0.15])
fig.update_yaxes(title_text="Mean Squared Error", row=3, col=1, range=[0, 0.15])
fig.update_xaxes(title_text="Training Epochs", row=3, col=1)
fig.update_layout(height=800, width=800)

# Plot training loss for each history object
plot_loss(fig, 1, {365:history_pretraining}, first_epoch, last_epoch, first_day)
plot_loss(fig, 2, train_histories, first_epoch, last_epoch, first_day)
plot_loss(fig, 3, train_histories_wo_pretraining, first_epoch, last_epoch, first_day)

fig.write_image('training_loss.png', scale=4)

fig.show()
